In [ ]:
import pandas as pd
from shapely import Point, LineString, Polygon, intersection
import geopandas as gpd
import math
import time


def get_visibility_result2(point, buildings, view_distance):
    crs = buildings.crs
    point_buffer = Point(point).buffer(view_distance)
    s = buildings.within(point_buffer)
    buildings_in_buffer = buildings.loc[s[s].index].reset_index(drop=True)
    buffer_exterior_ = list(point_buffer.exterior.coords)
    line_geometry = [LineString([point, ext]) for ext in buffer_exterior_]
    buffer_lines_gdf = gpd.GeoDataFrame(geometry=line_geometry)
    united_buildings = buildings_in_buffer.unary_union

    if united_buildings:
        splited_lines = buffer_lines_gdf['geometry'].apply(lambda x: x.difference(united_buildings))
    else:
        splited_lines = buffer_lines_gdf["geometry"]

    splited_lines_gdf = gpd.GeoDataFrame(geometry=splited_lines).explode(index_parts=True)
    splited_lines_list = []

    for u, v in splited_lines_gdf.groupby(level=0):
        splited_lines_list.append(v.iloc[0]['geometry'].coords[-1])
    circuit = Polygon(splited_lines_list)
    if united_buildings:
        circuit = circuit.difference(united_buildings)

    view_zone = gpd.GeoDataFrame(geometry=[circuit], crs=crs)
    return view_zone


builds = gpd.read_file('examples_data/tara_buildings.geojson').to_crs(32638)
p = Point(8278652.47, 7737142.18)
point = gpd.GeoDataFrame(geometry=[p], crs=3857).to_crs(32638)
view_zone = get_visibility_result2(point.geometry[0], builds, 500)

In [ ]:


from shapely import MultiPolygon


def get_visibility_result(mid_point, buildings, view_distance):
    def get_line_from_p_through_p(A: Point, B: Point, dist):
        direction = math.atan2(B.y - A.y, B.x - A.x)
        C_x = A.x + dist * math.cos(direction)
        C_y = A.y + dist * math.sin(direction)
        return LineString([Point(A.x, A.y), Point(C_x, C_y)])

    crs = buildings.crs
    point_buffer = Point(mid_point).buffer(view_distance)

    s = buildings.intersects(point_buffer)

    buildings_in_buffer = buildings.loc[s[s].index].reset_index(drop=True)
    builds_points_inside = [Point(coords) for geom in buildings_in_buffer.geometry.unary_union.geoms for coords in
                            geom.exterior.coords]
    united_buildings = buildings_in_buffer.unary_union

    lines_to_corners = [LineString([mid_point, ext]) for ext in builds_points_inside]
    lines_to_corners = gpd.GeoDataFrame(geometry=lines_to_corners, crs=crs)
    lines_to_corners = lines_to_corners['geometry'].apply(lambda x: x.difference(united_buildings))
    lines_to_corners = gpd.GeoDataFrame(geometry=lines_to_corners, crs=crs).explode(index_parts=True)

    points_to_build = pd.DataFrame()
    for u, v in lines_to_corners.groupby(level=0):
        points_to_build = pd.concat(
            [points_to_build, pd.DataFrame({'geometry': [Point(v.iloc[0].geometry.coords[-1])]})])

    lines_to_buf = [get_line_from_p_through_p(mid_point, p_obn_b, view_distance) for p_obn_b in builds_points_inside]

    buffer_exterior_ = list(point_buffer.exterior.coords)
    lines_to_buf2 = [LineString([mid_point, ext]) for ext in buffer_exterior_]

    lines_to_buf = gpd.GeoDataFrame(geometry=lines_to_buf + lines_to_buf2, crs=crs)

    united_buildings_buf = united_buildings.buffer(-0.005)
    lines_to_buf = lines_to_buf['geometry'].apply(lambda x: x.difference(united_buildings_buf))

    lines_to_buf = gpd.GeoDataFrame(geometry=lines_to_buf, crs=crs).explode(index_parts=True)

    for u, v in lines_to_buf.groupby(level=0):
        points_to_build = pd.concat(
            [points_to_build, pd.DataFrame({'geometry': [Point(v.iloc[0].geometry.coords[-1])]})])

    points_to_build.drop_duplicates(subset=['geometry'], inplace=True, keep='first')

    points_with_angle = []
    for point_to in points_to_build.geometry:
        angle = math.atan2(point_to.y - mid_point.y, point_to.x - mid_point.x)
        points_with_angle.append((point_to, angle))

    points_with_angle = [(p, round(angle, 3), p.distance(mid_point)) for p, angle in points_with_angle]
    points_with_angle.sort(key=lambda x: -x[1])

    new_points_with_angle = []
    point_pre_last = points_with_angle[-1]
    point_last = points_with_angle[0]

    new_tuple = (points_with_angle[0][0], points_with_angle[0][1], points_with_angle[0][2],
                 abs(point_pre_last[2] - points_with_angle[0][2]))
    new_points_with_angle.append(new_tuple)

    for i in range(1, len(points_with_angle)):
        current_point = points_with_angle[i]
        cur_angle = current_point[1]

        if cur_angle == point_last[1]:
            diff = abs(point_pre_last[2] - current_point[2])
            new_tuple = (current_point[0], current_point[1], current_point[2], diff)
            new_points_with_angle.append(new_tuple)
            point_last = current_point

        if cur_angle != point_last[1]:
            diff = abs(point_last[2] - current_point[2])
            new_tuple = (current_point[0], current_point[1], current_point[2], diff)
            new_points_with_angle.append(new_tuple)
            point_pre_last = point_last
            point_last = current_point

    new_points_with_angle.sort(key=lambda x: (-x[1], x[3]))

    result = Polygon([t[0] for t in new_points_with_angle])
    result = intersection(point_buffer, result)
    result = MultiPolygon([y for y in result.geoms if (
            y.geom_type == 'Polygon' or y.geom_type == 'MultiPolygon')]) if result.geom_type == 'GeometryCollection' else result

    result = gpd.GeoDataFrame(geometry=[result], crs=crs)
    return result


builds = gpd.read_file('examples_data/tara_buildings.geojson').to_crs(32638)
builds['geometry'] = builds.geometry.apply(lambda x: x.simplify(1))
p = Point(8278652.47, 7737142.18)
point = gpd.GeoDataFrame(geometry=[p], crs=3857).to_crs(32638)
view_zone_new = get_visibility_result(point.geometry[0], builds, 500)

In [ ]:

m1 = gpd.GeoDataFrame(geometry=view_zone.geometry.union(view_zone_new), crs=32638).explore(color='green')
gpd.GeoDataFrame(geometry=view_zone.geometry.difference(view_zone_new), crs=32638).explore(m=m1, color='red')
gpd.GeoDataFrame(geometry=view_zone_new.geometry.difference(view_zone), crs=32638).explore(m=m1, color='blue')
builds.explore(m=m1, color='yellow', style_kwds={'fillOpacity': 0.3})
point.explore(m=m1, color='purple', marker_kwds={'radius': 5})
m1

In [1]:
import pandas as pd
from shapely import Point, LineString, Polygon, intersection,MultiPolygon,MultiLineString
import geopandas as gpd
import math
import time
global lines
def get_visibility_from_point(mid_point: Point, buildings_union: MultiPolygon, buildings_union_buffered: MultiPolygon,
                              view_distance: int, crs: int):
    def get_line_from_a_thorough_b(A: Point, B: Point, dist):
        """
        Func to get line from point A thorough point B on dist
        """
        direction = math.atan2(B.y - A.y, B.x - A.x)
        C_x = A.x + dist * math.cos(direction)
        C_y = A.y + dist * math.sin(direction)
        return LineString([Point(A.x, A.y), Point(C_x, C_y)])
    print(1)
    point_buffer = Point(mid_point).buffer(view_distance)
    
    buildings_in_buffer = buildings_union.intersection(point_buffer)
    buildings_in_buffer = (
        MultiPolygon([y for y in buildings_in_buffer.geoms if (y.geom_type == "Polygon" or y.geom_type == "MultiPolygon")])
        if buildings_in_buffer.geom_type == "GeometryCollection"
        else buildings_in_buffer
    )
    # getting all building's points in buffer
    print(2)
    builds_points_inside = [
        Point(coords) for geom in buildings_in_buffer.geoms for coords in geom.exterior.coords
    ]
    print(3)
    united_buildings_buf = buildings_union_buffered.intersection(point_buffer)
    united_buildings_buf = (
        MultiPolygon([y for y in united_buildings_buf.geoms if (y.geom_type == "Polygon" or y.geom_type == "MultiPolygon")])
        if united_buildings_buf.geom_type == "GeometryCollection"
        else united_buildings_buf
    )
    print(4)
    # raytracing lines from mid point to building's corners
    lines_to_corners = MultiLineString([LineString([mid_point, ext]) for ext in builds_points_inside])
    print(44)
    global  lines
    lines = buildings_in_buffer
    return None
    lines_to_corners = lines_to_corners.difference(buildings_in_buffer)
    print(45)
    lines_to_corners = gpd.GeoDataFrame(geometry=lines_to_corners, crs=crs).explode(index_parts=True)
    
    print(22)
    # filter lines, removing all intersecting parts
    points_to_build = pd.DataFrame()
    for u, v in lines_to_corners.groupby(level=0):
        points_to_build = pd.concat(
            [points_to_build, pd.DataFrame({"geometry": [Point(v.iloc[0].geometry.coords[-1])]})]
        )
    print(5)
    # raytracing lines from mid point thorough building's corners to buffer limit
    lines_to_buf = [get_line_from_a_thorough_b(mid_point, p_obn_b, view_distance) for p_obn_b in builds_points_inside]
    print(6)
    buffer_exterior_ = list(point_buffer.exterior.coords)
    lines_to_buf2 = [LineString([mid_point, ext]) for ext in buffer_exterior_]

    lines_to_buf = gpd.GeoDataFrame(geometry=lines_to_buf + lines_to_buf2, crs=crs)
    print(7)
    # decreasing building size, due to geometry issues
    
    lines_to_buf = lines_to_buf["geometry"].apply(lambda x: x.difference(united_buildings_buf))

    lines_to_buf = gpd.GeoDataFrame(geometry=lines_to_buf, crs=crs).explode(index_parts=True)
    # filter lines, removing all intersecting parts
    for u, v in lines_to_buf.groupby(level=0):
        points_to_build = pd.concat(
            [points_to_build, pd.DataFrame({"geometry": [Point(v.iloc[0].geometry.coords[-1])]})]
        )
    print(8)
    points_to_build.drop_duplicates(subset=["geometry"], inplace=True, keep="first")

    # calculating the angle of each line to determine the connection order
    points_with_angle = []
    for point_to in points_to_build.geometry:
        angle = math.atan2(point_to.y - mid_point.y, point_to.x - mid_point.x)
        points_with_angle.append((point_to, angle))
    print(9)
    points_with_angle = [(p, round(angle, 3), p.distance(mid_point)) for p, angle in points_with_angle]
    points_with_angle.sort(key=lambda x: -x[1])

    # for the equal angles, it is necessary to determine the connection order.
    # Connecting not just nearest points, but points that are closer in distance from the center
    new_points_with_angle = []
    point_pre_last = points_with_angle[-1]
    point_last = points_with_angle[0]
    print(10)
    new_tuple = (
        points_with_angle[0][0],
        points_with_angle[0][1],
        points_with_angle[0][2],
        abs(point_pre_last[2] - points_with_angle[0][2]),
    )
    new_points_with_angle.append(new_tuple)
    print(11)
    for i in range(1, len(points_with_angle)):
        current_point = points_with_angle[i]
        cur_angle = current_point[1]

        if cur_angle == point_last[1]:
            diff = abs(point_pre_last[2] - current_point[2])
            new_tuple = (current_point[0], current_point[1], current_point[2], diff)
            new_points_with_angle.append(new_tuple)
            point_last = current_point

        if cur_angle != point_last[1]:
            diff = abs(point_last[2] - current_point[2])
            new_tuple = (current_point[0], current_point[1], current_point[2], diff)
            new_points_with_angle.append(new_tuple)
            point_pre_last = point_last
            point_last = current_point
    print(12)
    new_points_with_angle.sort(key=lambda x: (-x[1], x[3]))
    # creating polygon with properly ordered points
    result = Polygon([t[0] for t in new_points_with_angle])
    result = intersection(point_buffer, result)
    result = (
        MultiPolygon([y for y in result.geoms if (y.geom_type == "Polygon" or y.geom_type == "MultiPolygon")])
        if result.geom_type == "GeometryCollection"
        else result
    )

    result = gpd.GeoDataFrame(geometry=[result], crs=crs)
    return result

In [3]:
builds = gpd.read_file('builds.geojson').to_crs(32636)
points = gpd.read_file('points.geojson').to_crs(32636)

In [ ]:
view_distance=5000
points_view = points.geometry.buffer(view_distance).unary_union
s = builds.intersects(points_view)
buildings_in_buffer = builds.loc[s[s].index].reset_index(drop=True)
building_union = buildings_in_buffer.geometry.unary_union
building_union_buffer = building_union.buffer(-0.005)
crs = builds.crs
point = [point for point in points.geometry][0]

In [ ]:
res = get_visibility_from_point(point,building_union,building_union_buffer,view_distance,crs)

In [4]:
from joblib import Parallel, delayed


def calculate_visibility_catchment_area(points, buildings: gpd.GeoDataFrame, view_distance):
    points_view = points.geometry.buffer(view_distance).unary_union
    s = buildings.intersects(points_view)
    buildings_in_buffer = buildings.loc[s[s].index].reset_index(drop=True)
    building_union = buildings_in_buffer.geometry.unary_union
    building_union_buffer = building_union.buffer(-0.005)
    crs = buildings.crs
    point = [point for point in points.geometry][0]
    print('started')
    results = get_visibility_from_point(point,building_union,building_union_buffer,view_distance,crs)
    # results = Parallel(n_jobs=-1)(
    #     delayed(get_visibility_from_point)(point, building_union,building_union_buffer,view_distance,crs) for point in points)
    return results

res= calculate_visibility_catchment_area(points.iloc[:1],builds,5000)

started
1
2
3
4
44


In [12]:
gpd.GeoDataFrame(geometry=[lines],crs=32636).explore()

In [ ]:
import pandas as pd
from shapely import Point, LineString, Polygon, intersection
import geopandas as gpd
import math

